# Use Cases

In [1]:
%matplotlib inline
import bokeh
from bokeh.io import output_file, output_notebook
from bokeh.plotting import figure, show, ColumnDataSource
from bokeh.models import GeoJSONDataSource, HoverTool, CategoricalColorMapper, LinearColorMapper, ColorBar
from bokeh.palettes import viridis, inferno, OrRd, Category10
import geopandas as gpd
import pandas as pd
output_notebook()

Loading BokehJS ...

In [2]:
# load map
nyc_ipv = gpd.read_file('../data/processed/ipv.geojson')
nyc_ipv.columns = [col.replace(' ', '_') for col in nyc_ipv.columns]
colz = ['precinct', 'radio_runs', 'monthly_avg','lowest', 'highest', 'description', 'rank', 'borough']
nyc_ipv.sort_values(by='radio_runs', ascending=False).head(10)[colz]

precinct  radio_runs  monthly_avg  lowest  highest  \
46       75        6231   692.333333     606      814   
25       43        5221   580.111111     491      633   
28       46        5058   562.000000     480      599   
29       47        4953   550.333333     481      614   
45       73        4872   541.333333     482      600   
26       44        4435   492.777778     448      548   
22       40        4329   481.000000     422      520   
24       42        4244   471.555556     398      521   
33       52        4125   458.333333     412      487   
30       48        3852   428.000000     377      471   

                                          description  rank   borough  
46  The 75th Precinct serves the easternmost porti...   1st  brooklyn  
25  The 43rd Precinct serves the southeast section...   2nd     bronx  
28  The 46th Precinct serves the central part of t...   3rd     bronx  
29  The 47th Precinct serves northern portion of t...   4th     bronx  
45  The 73rd Precinct serves a northeastern area o...   5th  brooklyn  
26  The 44th Precinct serves 1.97 square miles of ...   6th     bronx  
22  The 40th Precinct is the southernmost precinct...   7th     bronx  
24  New York City's 42nd Precinct serves an area o...   8th     bronx  
33  The 52nd Precinct serves a northern portion of...   9th     bronx  
30  The 48th Precinct sits in the heart of the Bro...  10th     bronx

## Mapping

In [3]:
figures = {}

geo_source = GeoJSONDataSource(geojson=nyc_ipv.to_json())

color_mapper = LinearColorMapper(
    list(reversed(OrRd[9])), 
    low=1, 
    high=7000
)

fig = figure(
    title='Data behind the violence ',
    x_axis_location=None, 
    y_axis_location=None, 
)
fig.patches(
    xs='xs',
    ys='ys',
    alpha=0.9,
    source=geo_source, 
    color={
        'field': 'radio_runs',
        'transform': color_mapper
    }, 
    line_width=1, 
    line_alpha=0.5, 
    line_color='white'
)

hover = HoverTool(
    point_policy='follow_mouse',
    tooltips=(
        '<style>'
        'p {'
        'word-wrap: break-word;'
        '}'
        '</style>'
        '<div><b>Precinct</b>: @precinct</div>'
        '<div><b>Borough</b>: @borough</div>'
        '<div><b>Runs</b>: @radio_runs</div>'
        "<div style='width:200px'><p><b>Analysis</b>: @analysis</p></div>"

    )
)
fig.add_tools(hover)
fig.grid.grid_line_color = None

color_bar = bokeh.models.ColorBar(
    color_mapper=color_mapper,
    orientation='horizontal',
    border_line_color=None, 
    location=(0,0),
)

fig.xaxis.visible = False
fig.yaxis.visible = False
fig.grid.visible = False

fig.add_layout(
    color_bar, 
    'below'
)

fig.add_layout(
    bokeh.models.Title(
        text="Number of radio runs between Jan 2017 to Sept 2017", 
        align="center"
    ),
    "below"
)
figures['radio-runs'] = fig

show(fig)

## Automated Analysis

In [4]:
top_ten = nyc_ipv.sort_values(by='radio_runs', ascending=False).head(10)

for row, col in top_ten.iterrows():
    precinct = col['precinct']
    about = col['description']
    analysis = col['analysis']
    output = f"{about} {analysis}\n"
    print(output)

The 75th Precinct serves the easternmost portion of Brooklyn and envelopes East New York and Cypress Hills. Precinct 75 had a total of 6231 radio runs between January and September. An average of 692.3 monthly radio runs with months ranging from as low as 606 to high as 814. It ranked 1st among 77 precincts in total radio runs for 2017.

The 43rd Precinct serves the southeast section of the Bronx. There are four primary commercial strips in the precinct: Westchester Avenue, Castle Hill Avenue, White Plains Road, and Parkchester. Precinct 43 had a total of 5221 radio runs between January and September. An average of 580.1 monthly radio runs with months ranging from as low as 491 to high as 633. It ranked 2nd among 77 precincts in total radio runs for 2017.

The 46th Precinct serves the central part of the western Bronx. The precinct contains the Fordham, University Heights, Morris Heights and Mount Hope neighborhoods. Precinct 46 had a total of 5058 radio runs between January and Septem